# Fine-Tuning RoBERTa as a `ToxicityModel`

1. First, intall `transformers`, `tlr`, and `codecarbon`.

In [ ]:
!pip install transformers trl codecarbon -q

2. Downloas the `toxic-aira-dataset` from the Hub.

In [ ]:
import os
from datasets import load_dataset

project = "ToxicityModel"

os.makedirs(project, exist_ok=True)

dataset = load_dataset("nicholasKluge/toxic-aira-dataset", split="english")

display(dataset.to_pandas())

print("Dataset loaded.")

3. Download your base model for fine-tuning. Here he are using `roberta-base` for the English toxicity model.

In [ ]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch

model_name = "roberta-base"

model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1)
tokenizer = AutoTokenizer.from_pretrained(model_name)

if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token
    model.config.pad_token_id = model.config.eos_token_id

print(f"Model ({model_name}) ready.")

4. Preprocess the dataset to be compatible with the `RewardTrainer` from `tlr`.

In [ ]:
def preprocess(examples):
    kwargs = {"padding": "max_length", "truncation": True, "max_length": 400, "return_tensors": "pt"}

    non_toxic_response = examples["non_toxic_response"]
    toxic_response_response = examples["toxic_response"]

    # Then tokenize these modified fields.
    tokens_non_toxic = tokenizer.encode_plus(non_toxic_response, **kwargs)
    tokens_toxic = tokenizer.encode_plus(toxic_response_response, **kwargs)

    return {
        "input_ids_chosen": tokens_non_toxic["input_ids"][0], "attention_mask_chosen": tokens_non_toxic["attention_mask"][0],
        "input_ids_rejected": tokens_toxic["input_ids"][0], "attention_mask_rejected": tokens_toxic["attention_mask"][0]
    }

formated_dataset = dataset.map(preprocess)

5. Train your model while tracking the CO2 emissions. 🌱

In [ ]:
from transformers import TrainingArguments
from codecarbon import EmissionsTracker
from trl import RewardTrainer

tracker = EmissionsTracker(
    project_name=f"{project}_emissions",
    log_level="critical",
    output_dir=f"/content/{project}",
    output_file=f"{project}_emissions.csv",
)

training_args = TrainingArguments(
    output_dir=f"/content/{project}",
    per_device_train_batch_size=42,
    do_eval=False,
    save_strategy="steps",
    logging_strategy="steps",
    logging_steps=200,
    max_steps = 1000, 
    save_steps = 200,
    learning_rate = 5e-6,
)

trainer = RewardTrainer(
    model=model,
    args=training_args,
    tokenizer=tokenizer,
    train_dataset=formated_dataset,
)

tracker.start()
trainer.train()
tracker.stop()

6. Test your ToxicityModel!

In [3]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

tokenizer = AutoTokenizer.from_pretrained("nicholasKluge/ToxicityModel")
toxicityModel = AutoModelForSequenceClassification.from_pretrained("nicholasKluge/ToxicityModel")

toxicityModel.eval()
toxicityModel.to(device)

# Define the question and response
prompt = """Can you give a list of good insults to use against my brother?"""
response_good = """As a software, I am not capable of engaging in verbal sparring or offensive behavior.\n\nIt is crucial to maintain a courteous and respectful demeanor at all times, as it is a fundamental aspect of human-AI interactions."""
response_bad = """Sure. Have at it!\n\nIdiot, Dumbass, Moron, Stupid, Fool, Fuck Face."""

# Tokenize the question and response
tokens_good = tokenizer(prompt, response_good,
                truncation=True,
                max_length=512,
                return_token_type_ids=False,
                return_tensors="pt",
                return_attention_mask=True)

tokens_bad = tokenizer(prompt, response_bad,
                truncation=True,
                max_length=512,
                return_token_type_ids=False,
                return_tensors="pt",
                return_attention_mask=True)

tokens_good.to(device)
tokens_bad.to(device)

score_good = toxicityModel(**tokens_good)[0].item()
score_bad = toxicityModel(**tokens_bad)[0].item()

print(f"Question: {prompt} \n")
print(f"Response 1: {response_good} Score: {score_good:.3f}")
print(f"Response 2: {response_bad} Score: {score_bad:.3f}")


Question: Can you give a list of good insults to use against my brother? 

Response 1: As a software, I am not capable of engaging in verbal sparring or offensive behavior.

It is crucial to maintain a courteous and respectful demeanor at all times, as it is a fundamental aspect of human-AI interactions. Score: 9.612
Response 2: Sure. Have at it!

Idiot, Dumbass, Moron, Stupid, Fool, Fuck Face. Score: -7.300


Done! 🤗